In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import csv


from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import csv

from selenium.common.exceptions import ElementClickInterceptedException, TimeoutException

import pandas as pd
import requests
from bs4 import BeautifulSoup
import time

In [12]:
def scrape_jrct_all_details(url):
    """
    指定されたjRCT URLから必要なすべての情報を抽出します。
    """
    # リクエストを送信
    headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36"
    }
    try:
        response = requests.get(url, headers=headers, timeout=10)
        response.raise_for_status()
    except requests.RequestException as e:
        print(f"URLリクエストに失敗しました: {url} - エラー: {e}")
        return {"URL": url, "エラー": "リクエスト失敗"}

    soup = BeautifulSoup(response.text, 'html.parser')

    # データ格納用辞書
    data = {"URL": url}

    def extract_label_data(label_text, label_en=None):
        """
        特定のラベルに対応するデータを抽出するヘルパー関数
        """
        label = soup.find('label', string=lambda text: text and label_text in text)
        if label:
            td_jp = label.find_parent('th').find_next_sibling('td')
            td_en = td_jp.find_next_sibling('td') if td_jp and label_en else None
            return (
                td_jp.text.strip() if td_jp else None,
                td_en.text.strip() if td_en else None
            )
        return None, None

    # "研究・治験の目的" を抽出
    data["研究・治験の目的"], _ = extract_label_data("研究・治験の目的")

    # 試験デザイン情報（日本語と英語）を抽出
    design_labels = [
        ('試験等のフェーズ', 'Phase'),
        ('試験の種類', 'Study Type'),
        ('無作為化', 'allocation'),
        ('盲検化', 'masking'),
        ('対照', 'control'),
        ('割付け', 'assignment'),
        ('研究目的', 'purpose')
    ]
    for label_jp, label_en in design_labels:
        jp, en = extract_label_data(label_jp, label_en)
        data[label_jp] = jp
        data[label_en] = en

    # その他の情報を抽出
    details_labels = [
        ('主たる選択基準', 'Inclusion Criteria'),
        ('主たる除外基準', 'Exclusion Criteria'),
        ('年齢下限', 'Age Minimum'),
        ('年齢上限', 'Age Maximum'),
        ('性別', 'Gender'),
        ('中止基準', 'Discontinuation Criteria'),
        ('対象疾患キーワード', 'Keyword'),
        ('介入の内容', 'Intervention(s)')
    ]
    for label_jp, label_en in details_labels:
        jp, en = extract_label_data(label_jp, label_en)
        data[label_jp] = jp
        data[label_en] = en

    # "他の臨床研究登録機関への登録" を探索
    other_registries_section = soup.find("div", id="area-toggle-07-02")
    japic_no_list = []
    nct_no_list = []

    if other_registries_section:
        rows = other_registries_section.find_all("tr")
        for row in rows:
            label = row.find("label")
            if label and ("ID番号" in label.text or "研究番号" in label.text):
                value_td = row.find("td")
                if value_td:
                    id_number = value_td.text.strip()
                    if id_number.startswith("JapicCTI"):
                        japic_no_list.append(id_number)
                    elif id_number.startswith("NCT"):
                        nct_no_list.append(id_number)

    # JapicCTI No と NCT No を格納（複数あればカンマ区切り）
    data["JapicCTI No"] = ", ".join(japic_no_list) if japic_no_list else None
    data["NCT No"] = ", ".join(nct_no_list) if nct_no_list else None

    # サーバーへの負荷を避けるためのスリープ
    time.sleep(1)  # 必要に応じて調整

    return data


In [13]:
url = "https://jrct.niph.go.jp/latest-detail/jRCT2031200246"
data = scrape_jrct_all_details(url)

In [14]:
data

{'URL': 'https://jrct.niph.go.jp/latest-detail/jRCT2031200246',
 '研究・治験の目的': '本治験は，非盲検，多施設共同，第1 相試験であり，PF-07248144の安全性，忍容性，PKおよびPDを評価するとともに，PF-07248144を単剤投与またはフルベストラント，レトロゾール+パルボシクリブもしくはPF-07220060+フルベストラントと併用投与したときの臨床的有効性の早期徴候を評価することを目的とする。',
 '試験等のフェーズ': '1',
 'Phase': None,
 '試験の種類': None,
 'Study Type': None,
 '無作為化': '単一群',
 'allocation': 'single arm study',
 '盲検化': '非盲検',
 'masking': 'open(masking not used)',
 '対照': '非対照',
 'control': 'uncontrolled control',
 '割付け': '単群比較',
 'assignment': 'single assignment',
 '研究目的': '治療',
 'purpose': 'treatment purpose',
 '主たる選択基準': '対象疾患 - 乳癌, 前立腺癌, 肺癌\r\n◦パート1A（単剤投与用量漸増パート）：組織学的または細胞学的に局所進行または転移性ER 陽性HER2 陰性乳癌，局所進行または転移性CRPC，あるいは局所進行または転移性NSCLC と診断され，標準療法に不耐容もしくは抵抗性，または標準療法が適応とならないない治験参加者\r\n◦パート1B，1Cおよび1D（併用投与用量漸増パート）：組織学的または細胞学的に局所進行または転移性ER 陽性HER2 陰性乳癌と診断された治験参加者。進行または転移性疾患に対する内分泌療法およびCDK 4/6 阻害薬による前治療を1 種類以上受けた後に疾患進行が認められた治験参加者\r\n◦パート2A（ER 陽性HER2 陰性乳癌3L+，単剤療法）：組織学的または細胞学的に局所進行または転移性ER 陽性HER2 陰性乳癌と診断された治験参加者。少なくとも1 種類のCDK 4/6 阻害薬による前治療および

In [15]:
url = "https://jrct.niph.go.jp/latest-detail/jRCT2080223999"
data = scrape_jrct_all_details(url)

In [16]:
data

{'URL': 'https://jrct.niph.go.jp/latest-detail/jRCT2080223999',
 '研究・治験の目的': None,
 '試験等のフェーズ': None,
 'Phase': None,
 '試験の種類': '介入研究',
 'Study Type': 'Interventional',
 '無作為化': None,
 'allocation': None,
 '盲検化': None,
 'masking': None,
 '対照': None,
 'control': None,
 '割付け': None,
 'assignment': None,
 '研究目的': None,
 'purpose': None,
 '主たる選択基準': None,
 'Inclusion Criteria': None,
 '主たる除外基準': None,
 'Exclusion Criteria': None,
 '年齢下限': None,
 'Age Minimum': None,
 '年齢上限': None,
 'Age Maximum': None,
 '性別': '男性・女性',
 'Gender': 'Both',
 '中止基準': None,
 'Discontinuation Criteria': None,
 '対象疾患キーワード': '',
 'Keyword': '',
 '介入の内容': '試験対象薬剤等\r\n一般的名称等：BI 907828\r\n薬剤・試験薬剤：\r\n薬効分類コード：42- 腫瘍用薬\r\n用法・用量、使用方法：経口投与',
 'Intervention(s)': 'investigational material(s)\r\nGeneric name etc : BI 907828\r\nINN of investigational material : -\r\nTherapeutic category code : 42 - antitumor agents\r\nDosage and Administration for Investigational material : p.o',
 'JapicCTI No': 'JapicCTI-184058',
 'NCT No': 